In [1]:
%%html
<style>
.cell, .CodeMirror pre{ 
    font-size: 200%;
    line-height: 150%;
}
</style>

# Face Recognition

Face recognition is a widely studies application in comptuer vision.
There are several types of face recognition problem, such as (in increasing order of difficulty)
* Given training examples of a specific person, verify if a new image is likely to be that person.
* Given training examples of many people, decide which person a new image represents.
* Given a large set of images identify which images are of the same people.

In this part we'll look at a classic technique called *Eigenfaces* and see how it can be used to help solve these problems. Eigenfaces are an application of PCA to image data, and can be used to represent face images in a (relatively) low-dimensional space.

## References

L. Sirovich and M. Kirby [Low-Dimensional Procedure for the Characterisation of Human Faces](https://www.osapublishing.org/josaa/abstract.cfm?uri=josaa-4-3-519) Jnl. Optical Society of America A, 4(3), pages 519-524

M. Turk and A. Pentland [Face Recognition using Eigenfaces](https://ieeexplore.ieee.org/document/139758/) Int. Conf. Computer Vision 1991, pages 103-108

# PCA on Images

We've seen PCA in 2D, and the maths remains the same in higher dimensions.
We'll use a small subset (500 images) from the aligned [CelebA](http://mmlab.ie.cuhk.edu.hk/projects/CelebA.html) data set.
This is formed from another data set, [Labelled Faces in the Wild](http://vis-www.cs.umass.edu/lfw/) which contains images of celebrites, politicians, and so forth with ground truth identity information.
The aligned CelebA data set has the faces lined up so that the eyes are in the same place in the image, and all the images are the same size (\\(178 \times 218\\) pixels).
Since these are colour images, each pixel has 3 values, and so we can think of each image as a point in \\(178 \times 218 \times 3 = 116,412\\) dimensional space.

PCA proceeds much as in the 2D case, but we'll need a slight modification to cope with this very high-dimensional data.

We first need to read the images in, and convert them to 1D vectors.


In [2]:
%matplotlib inline
import numpy
import matplotlib.pyplot as plt
import cv2
import math

n = 500 # Number of samples
d = 178*218*3 # Number of dimensions (pixels) per sample

F = numpy.zeros([n,d]) # faces, one per row

for i in range(0,n):
    imgFile = 'celebA/'+ format(i+1, '06d') + '.jpg'
    image = cv2.imread(imgFile, cv2.IMREAD_COLOR)
    F[i, :] = image.flatten()/255.0
    cv2.imshow('Display', image)
    cv2.waitKey(10)

# Compute mean
m = numpy.mean(F, 0)
Z = F - m

# Visualise the average image
meanImg = m.reshape(218, 178, 3)
cv2.imshow('Display', meanImg)
cv2.waitKey()

cv2.destroyAllWindows()

## Covariance Computation

The next step is to compute the covariance,
\\[
C = \frac{1}{n-1}Z^TZ
\\]

However, with the high dimensionality of the data we have a problem. The matrix \\(Z\\) is \\(500 \times 116,412\\), so \\(C\\) will be \\(116,412 \times 116,412\\), or 13,551,753,744 values. 
At 1 byte per value, that's 13.5 GB of storage - and even 4 byte floats would need nearly 55 GB to *store*, let alone compute eigenvectors from.

## The 'Transpose Trick'

Fortunately there is a way around this, which arises from the mathematical definition of an eigenvector.
If we ignore the factor of \\(\frac{1}{n-1}\\) we have
\\[
\begin{align}
Cv &= \lambda v \\
Z^TZv &= \lambda v\\
ZZ^TZv &= \lambda Zv\\
ZZ^T(Zv) &= \lambda (Zv)
\end{align}
\\]
So if \\(v\\) is an eigenvector of \\(C\\) with eigenvalue \\(\lambda\\), then \\(Zv\\) is an eigenvector of 
\\[
C' = ZZ^T
\\]
with the same eigenvalue.
This means that we can swap our dimensions and our samples, and still do the same analysis.

**Question: Why is it OK to ignore the factor \\(\frac{1}{n-1}\\)? What factor should we use for \\(C'\\)?**

This *transpose trick* is useful whenever you have more dimensions to your data than samples, which is almost always the case when your samples are images.

The other change to the PCA presented eariler is that we use `eigh` rather than `eig`. 
The `eigh` function has some specific properties:
- It only works for Hermetian or real symmetric square matrices
- It returns the eigenvalues in order from smallest to largest

The covariance matrix is square and symmetric, so we can apply `eigh`, and the ordering is useful since `eig` is not guaranteed to return the values in any particular order. 
We do, however, have to reverse the order of the results.

Once we have a vector, \\(V\\), of eigenvectors, the eigenfaces are found as the rows of the matrix
\\[
U = V^TZ,
\\]
and these are normalised so that they are unit vectors.

In [3]:
C = numpy.matmul(Z, numpy.transpose(Z))/(n-1)

eVal, eVec = numpy.linalg.eigh(C)

# Reverse the order so they go from largest to smallest
e = eVal[::-1]
V = eVec[:,::-1]

# Eigen faces - need normalising
U = numpy.matmul(numpy.transpose(V), Z)
for i in range(0,n):
    U[i,:] /= numpy.linalg.norm(U[i,:])

The matrix \\(U\\) has 500 rows, each of which can be interpreted as an image (with approprite scaling).
These are the principal components of the face data set, and are the Eigenfaces that give the method its name.

In [4]:
for i in range(0,10):
    ef = U[i,:].reshape(218, 178, 3)/max(abs(U[i,:])) + 0.5
    cv2.imshow('EigenFaces', ef)
    cv2.waitKey()
    
cv2.destroyAllWindows()

A given face image can be represented as the mean face plus a weighted sum of the eigenfaces (each row of the matrix being an eigenface). The weights are given by
\\[
w = U(f-\mu)
\\]
where \\(U\\) is the matrix of eigenfaces, \\(f\\) is the face as a vector, and \\(\mu\\) is the mean face vector.
These weights can be used as a low-dimensional representation of the faces, and we can choose to discard those corresponding to small egienvalues to further reduce the space.

For our training faces, \\(f - \mu\\) corresponds to the rows of \\(Z\\). We can see this by reconstructing a face from the database:

In [5]:
f = 17 # Index of a face in the database

original = (Z[f,:] + m).reshape(218, 178, 3)
cv2.imshow('Original', original)
cv2.waitKey()

w = numpy.matmul(U, Z[f,:])

recon = m.copy()
cv2.imshow('Reconstruction', recon.reshape(218, 178, 3))
cv2.waitKey()
    
for i in range(0,n):
    recon += w[i]*U[i, :]
    cv2.imshow('Reconstruction', recon.reshape(218, 178, 3))
    cv2.waitKey(100)
    
cv2.waitKey()
    

cv2.destroyAllWindows()

In [6]:
cv2.destroyAllWindows()

In [8]:
U.shape

(500, 116412)